# Optimize Initial Conditions
## Differential Evolution SciPy

In [1]:
from scipy.optimize import brute
import numpy as np
from datetime import datetime,timedelta
import pandas as pd
from scipy.optimize import differential_evolution

# Load Solver

In [2]:
LoadBH=True
if LoadBH:
    import LearnerICRayNoLoadBH as L 
else:
    import LearnerICRayNoLoad as L 

# Load Data

In [3]:
def load_confirmed(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/confirmados.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

def load_dead(state, start_date):
    dateparse = lambda x: datetime.strptime(x, '%Y-%m-%d')
    df = pd.read_csv('./data/mortes.csv',delimiter=',',parse_dates=True, date_parser=dateparse)
    y=[]
    x=[]
    for i in range(0,len(df.date)):
        y.append(df[state].values[i])
        x.append(df.date.values[i])
    df2=pd.DataFrame(data=y,index=x,columns=[""])
    df2=df2[start_date:]
    del x,y,df,dateparse
    return df2

# Initial parameters

In [4]:
dfparam = pd.read_csv("data/param.csv")
dfparam

state  start-date  prediction-range         s0  e0  a0   i0   r0   d0  \
0    SP  2020-03-15               200  8000000.0   0   0  800  300  250   
1    ES  2020-04-01               200   475000.0   0   0   50  250   50   
2    MG  2020-04-01               200  1100000.0   0   0  200  250   40   
3    RJ  2020-03-20               200   700000.0   0   0  800  250   50   
4    CE  2020-03-20               200   800000.0   0   0  800  250   50   
5    PE  2020-03-20               200   700000.0   0   0  800  250  100   
6    AM  2020-03-20               200   700000.0   0   0  800  250  100   

   START  RATIO  WCASES  WREC  
0    100   0.15    0.55  0.01  
1    100   0.15    0.65  0.01  
2    100   0.15    0.55  0.01  
3    100   0.15    0.50  0.01  
4    100   0.15    0.50  0.01  
5    100   0.15    0.50  0.01  
6    100   0.15    0.50  0.01

# Data for States

In [5]:
df = pd.read_csv("data/dados_total_estados.csv")
df

index        date state   city place_type  confirmed  deaths  \
0          0  2020-06-06    SE  TOTAL      state       8972     208   
1          1  2020-06-05    SE  TOTAL      state       8577     198   
2          2  2020-06-04    SE  TOTAL      state       8200     186   
3          3  2020-06-03    SE  TOTAL      state       7989     180   
4          4  2020-06-02    SE  TOTAL      state       7555     172   
...      ...         ...   ...    ...        ...        ...     ...   
2244  158210  2020-03-11    BA  TOTAL      state          3       0   
2245  158211  2020-03-10    BA  TOTAL      state          2       0   
2246  158212  2020-03-09    BA  TOTAL      state          2       0   
2247  158213  2020-03-07    BA  TOTAL      state          2       0   
2248  158214  2020-03-06    BA  TOTAL      state          1       0   

      order_for_place  is_last      popEst  city_ibge_code  \
0                  74     True   2298696.0            28.0   
1                  73    False   2298696.0            28.0   
2                  72    False   2298696.0            28.0   
3                  71    False   2298696.0            28.0   
4                  70    False   2298696.0            28.0   
...               ...      ...         ...             ...   
2244                5    False  14873064.0            29.0   
2245                4    False  14873064.0            29.0   
2246                3    False  14873064.0            29.0   
2247                2    False  14873064.0            29.0   
2248                1    False  14873064.0            29.0   

      confirmed_per_100k_inhabitants  death_rate  
0                          390.30824      0.0232  
1                          373.12459      0.0231  
2                          356.72399      0.0227  
3                          347.54487      0.0225  
4                          328.66460      0.0228  
...                              ...         ...  
2244                         0.02017      0.0000  
2245                         0.01345      0.0000  
2246                         0.01345      0.0000  
2247                         0.01345      0.0000  
2248                         0.00672      0.0000  

[2249 rows x 13 columns]

# Functions for Optimization

In [6]:
from scipy.integrate import odeint
import os
import sys
import io
import ray
import gc
import tensorflow as tf

def create_f(state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):
                
    def fobjective(point):
        
        dead=  load_dead(state,date)
        data = load_confirmed(state,date)*(1-ratio)-dead
        
        cleanRecovered=False
        s0, deltaDate, i0, weigthCases, weigthRecov = point
        end_date=datetime.strptime(date, "%Y-%m-%d") + timedelta(days=+int(deltaDate))
                    
        f=L.Learner.remote(state, end_date.strftime("%Y-%m-%d"), predict_range,\
                           s0, e0, a0, i0, r0, d0, startNCases, ratio, weigthCases, weigthRecov, \
                           cleanRecovered, version, data, dead, savedata=False)
        result = f.train.remote() 
        result = ray.get(result) 

        del end_date,cleanRecovered, data, dead, point, f         

        gc.collect()

        return result
    return fobjective

In [7]:
@ray.remote(memory=100 * 1024 * 1024)
def opt(state,s0,i0,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version):

    bounds=[(0.8*s0,1.2*s0),(-10,10),(0.8*i0,1.2*i0),\
              (0.3,0.7),(0.001,0.05)]
    f=create_f(state,e0,a0,r0,d0,date,startNCases, ratio, predict_range, version)
    result = differential_evolution(f, bounds)

    return result.x

# Main Code

In [8]:
states=['SP','ES','MG','RJ','PE','CE','AM']
allStates=True
version="1002"
ray.shutdown()
GB=1024*1024*1024
MB=1024*1024
import cupy
ray.init(object_store_memory=500*MB,memory=2*GB,lru_evict=True,\
         driver_object_store_memory=50*MB,num_gpus=12,num_cpus=7)
gc.enable()

runID=[]
if allStates:
    for state in states:
    #for districtRegion in DRS:
    #remove previous history file
        strFile='./results/history_'+state+version+'.csv'
        if os.path.isfile(strFile):
            os.remove(strFile)
        query = dfparam.query('state == "{}"'.format(state)).reset_index()
        parameters = np.array(query.iloc[:, 2:])[0]
        startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
        f_remote=opt.remote(state,s0,i0,e0,a0,r0,d0,startdate,startNCases, \
                                                    ratio, predict_range, version)
        runID.append(f_remote)
else:
    state = "ES" 
    #remove previous history file
    strFile='./results/history_'+state+version+'.csv'
    if os.path.isfile(strFile):
        os.remove(strFile)
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    start_date,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    f_remote=opt.remote(state,s0,i0,e0,a0,r0,d0,startdate,startNCases, \
                                                ratio, predict_range, version)
    runID.append(f_remote)



2020-06-15 18:06:17,424	INFO resource_spec.py:212 -- Starting Ray with 1.95 GiB memory available for workers and up to 0.49 GiB for objects. You can adjust these settings with ray.init(memory=<bytes>, object_store_memory=<bytes>).
2020-06-15 18:06:17,906	INFO services.py:1170 -- View the Ray dashboard at localhost:8268


In [ ]:
optimal=ray.get(runID)

(pid=142729) basinhopping step 0: f 1.72904e+07
(pid=142702) basinhopping step 0: f 7.18536e+07
(pid=142747) basinhopping step 0: f 5.91355e+08
(pid=142702) basinhopping step 1: f 7.18536e+07 trial_f 8.96558e+07 accepted 0  lowest_f 7.18536e+07
(pid=142702) basinhopping step 2: f 7.02701e+07 trial_f 7.02701e+07 accepted 1  lowest_f 7.02701e+07
(pid=142702) found new global minimum on step 2 with function value 7.02701e+07
(pid=142716) basinhopping step 0: f -9.18875e+11
(pid=142702) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=142702)   warnings.warn(warning_msg, ODEintWarning)
(pid=142733) basinhopping step 0: f -1.49662e+12
(pid=142747) basinhopping step 1: f 5.86118e+08 trial_f 5.86118e+08 accepted 1  lowest_f 5.86118e+08
(pid=142747) found new global minimum on step 1 with function value 5.86118e+08
(pid=142862) 

(pid=142733) basinhopping step 8: f -1.49662e+12 trial_f 2.86441e+06 accepted 0  lowest_f -1.49662e+12
(pid=142883) basinhopping step 2: f -4.44801e+11 trial_f 8.16202e+07 accepted 0  lowest_f -4.44801e+11
(pid=142883) basinhopping step 3: f -4.44801e+11 trial_f 8.18963e+07 accepted 0  lowest_f -4.44801e+11
(pid=142706) basinhopping step 9: f -1.90793e+11 trial_f 1.36889e+09 accepted 0  lowest_f -1.90793e+11
(pid=142729) basinhopping step 10: f -9.27426e+10 trial_f 1.84069e+08 accepted 0  lowest_f -9.27426e+10
(pid=142862) basinhopping step 8: f -4.904e+11 trial_f -4.904e+11 accepted 1  lowest_f -4.904e+11
(pid=142862) found new global minimum on step 8 with function value -4.904e+11
(pid=142733) basinhopping step 9: f -1.49662e+12 trial_f 5.44563e+09 accepted 0  lowest_f -1.49662e+12
(pid=142883) basinhopping step 4: f -4.44801e+11 trial_f 1.10526e+08 accepted 0  lowest_f -4.44801e+11
(pid=142733) warning: basinhopping: local minimization failure
(pid=142733) basinhopping step 10: f -

(pid=150593) basinhopping step 3: f -7.18979e+13 trial_f 3.35308e+09 accepted 0  lowest_f -7.18979e+13
(pid=150593) basinhopping step 4: f -7.18979e+13 trial_f -7.18979e+13 accepted 1  lowest_f -7.18979e+13
(pid=142886) basinhopping step 9: f -2.06899e+11 trial_f 3.69537e+07 accepted 0  lowest_f -2.06899e+11
(pid=142876) basinhopping step 6: f 9.97931e+07 trial_f 1.59754e+08 accepted 0  lowest_f 9.97931e+07
(pid=142886) basinhopping step 10: f -2.06899e+11 trial_f 5.35351e+10 accepted 0  lowest_f -2.06899e+11
(pid=150592) basinhopping step 0: f 1.44269e+07
(pid=150394) basinhopping step 4: f 7.81391e+07 trial_f 7.81391e+07 accepted 1  lowest_f 7.81391e+07
(pid=150394) found new global minimum on step 4 with function value 7.81391e+07
(pid=142882) basinhopping step 5: f -1.77924e+12 trial_f 1.87007e+09 accepted 0  lowest_f -1.77924e+12
(pid=150394) basinhopping step 5: f 7.81391e+07 trial_f 4.05883e+08 accepted 0  lowest_f 7.81391e+07
(pid=150394) basinhopping step 6: f 7.81391e+07 tria

(pid=3959) basinhopping step 8: f -3.39798e+11 trial_f 8.38889e+07 accepted 0  lowest_f -3.39798e+11
(pid=4169) basinhopping step 5: f -4.2554e+11 trial_f 1.47366e+09 accepted 0  lowest_f -4.2554e+11
(pid=3958) basinhopping step 4: f -5.0924e+11 trial_f -5.0924e+11 accepted 1  lowest_f -5.0924e+11
(pid=3958) found new global minimum on step 4 with function value -5.0924e+11
(pid=4169) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=4169)   warnings.warn(warning_msg, ODEintWarning)
(pid=150593) basinhopping step 10: f -7.18979e+13 trial_f 3.05861e+10 accepted 0  lowest_f -7.18979e+13
(pid=4168) basinhopping step 4: f -1.86009e+11 trial_f -1.86009e+11 accepted 1  lowest_f -1.86009e+11
(pid=4168) found new global minimum on step 4 with function value -1.86009e+11
(pid=4168) /home/ats4i/anaconda3/lib/python3.7/site-packages

(pid=6707) warning: basinhopping: local minimization failure
(pid=6707) basinhopping step 7: f -7.17471e+11 trial_f -1.68263e+10 accepted 0  lowest_f -7.17471e+11
(pid=9011) basinhopping step 5: f -2.95051e+11 trial_f -2.85293e+11 accepted 0  lowest_f -2.95051e+11
(pid=9718) warning: basinhopping: local minimization failure
(pid=9718) basinhopping step 1: f -7.38167e+11 trial_f -7.38167e+11 accepted 1  lowest_f -7.38167e+11
(pid=9718) found new global minimum on step 1 with function value -7.38167e+11
(pid=9719) warning: basinhopping: local minimization failure
(pid=9719) basinhopping step 2: f -6.50151e+10 trial_f 2.0215e+07 accepted 0  lowest_f -6.50151e+10
(pid=6707) basinhopping step 8: f -7.17471e+11 trial_f 1.79538e+07 accepted 0  lowest_f -7.17471e+11
(pid=8389) basinhopping step 6: f -7.07735e+11 trial_f -7.07735e+11 accepted 1  lowest_f -7.07735e+11
(pid=8389) found new global minimum on step 6 with function value -7.07735e+11
(pid=9719) basinhopping step 3: f -6.50151e+10 tri

...

(pid=76219) basinhopping step 5: f -1.23921e+11 trial_f 1.77715e+07 accepted 0  lowest_f -1.23921e+11
(pid=76219) basinhopping step 6: f -3.88451e+11 trial_f -3.88451e+11 accepted 1  lowest_f -3.88451e+11
(pid=76219) found new global minimum on step 6 with function value -3.88451e+11
(pid=76220) basinhopping step 2: f -2.68382e+11 trial_f 1.35602e+08 accepted 0  lowest_f -2.68382e+11
(pid=76220) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=76220)   warnings.warn(warning_msg, ODEintWarning)
(pid=75554) basinhopping step 8: f -9.22193e+11 trial_f 1.57257e+09 accepted 0  lowest_f -9.22193e+11
(pid=76169) basinhopping step 3: f -8.62145e+11 trial_f -8.62145e+11 accepted 1  lowest_f -8.62145e+11
(pid=76169) found new global minimum on step 3 with function value -8.62145e+11
(pid=75553) warning: basinhopping: local minimiz

(pid=76762) basinhopping step 2: f -4.74715e+11 trial_f 1.28746e+09 accepted 0  lowest_f -4.74715e+11
(pid=76647) basinhopping step 3: f -3.01872e+13 trial_f 1.14579e+10 accepted 0  lowest_f -3.01872e+13
(pid=76734) basinhopping step 7: f -2.09482e+11 trial_f 2.43673e+07 accepted 0  lowest_f -2.09482e+11
(pid=76646) basinhopping step 7: f 1.21458e+08 trial_f 1.24256e+09 accepted 0  lowest_f 1.21458e+08
(pid=76735) basinhopping step 3: f -2.51894e+11 trial_f 2.5924e+10 accepted 0  lowest_f -2.51894e+11
(pid=76780) basinhopping step 0: f -6.3955e+11
(pid=76762) basinhopping step 3: f -4.74715e+11 trial_f 1.34077e+08 accepted 0  lowest_f -4.74715e+11
(pid=76762) basinhopping step 4: f -4.74715e+11 trial_f 1.33328e+08 accepted 0  lowest_f -4.74715e+11
(pid=76762) basinhopping step 5: f -4.74715e+11 trial_f 2.18116e+11 accepted 0  lowest_f -4.74715e+11
(pid=76647) basinhopping step 4: f -3.01872e+13 trial_f 7.39413e+08 accepted 0  lowest_f -3.01872e+13
(pid=76780) basinhopping step 1: f -6.

(pid=76780) basinhopping step 9: f -6.3955e+11 trial_f 1.72617e+08 accepted 0  lowest_f -6.3955e+11
(pid=76968) basinhopping step 3: f -1.59278e+11 trial_f 1.29905e+08 accepted 0  lowest_f -1.59278e+11
(pid=76902) basinhopping step 4: f -3.16908e+11 trial_f -3.16908e+11 accepted 1  lowest_f -3.16908e+11
(pid=76902) found new global minimum on step 4 with function value -3.16908e+11
(pid=76968) /home/ats4i/anaconda3/lib/python3.7/site-packages/scipy/integrate/odepack.py:248: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
(pid=76968)   warnings.warn(warning_msg, ODEintWarning)
(pid=76968) /home/ats4i/Desktop/corona/dataAndModelsCovid19/statesBrazil/LearnerICRayNoLoadBH.py:79: RuntimeWarning: overflow encountered in square
(pid=76968)   l1 = np.mean((res[ix[0],3] - data.values[ix])**2)
(pid=76968) /home/ats4i/Desktop/corona/dataAndModelsCovid19/statesBrazil/LearnerICRayNoLoadBH.py:80: RuntimeWarning: overfl

(pid=77038) basinhopping step 0: f -2.66202e+11
(pid=77122) basinhopping step 0: f -5.28219e+11
(pid=76903) warning: basinhopping: local minimization failure
(pid=76903) basinhopping step 8: f -6.43862e+11 trial_f 1.67755e+06 accepted 0  lowest_f -6.43862e+11
(pid=76781) basinhopping step 10: f 9.47126e+07 trial_f 7.95244e+08 accepted 0  lowest_f 9.47126e+07
(pid=77121) basinhopping step 0: f 2.23593e+08
(pid=77122) basinhopping step 1: f -5.28219e+11 trial_f 1.49676e+10 accepted 0  lowest_f -5.28219e+11
(pid=77038) basinhopping step 1: f -2.66202e+11 trial_f 1.1053e+07 accepted 0  lowest_f -2.66202e+11
(pid=77108) basinhopping step 4: f 1.21154e+08 trial_f 1.21798e+08 accepted 0  lowest_f 1.21154e+08
(pid=77121) basinhopping step 1: f 2.23593e+08 trial_f 2.41201e+10 accepted 0  lowest_f 2.23593e+08
(pid=77037) basinhopping step 8: f 1.79538e+07 trial_f 1.64582e+08 accepted 0  lowest_f 1.79538e+07
(pid=77121) basinhopping step 2: f 2.23593e+08 trial_f 3.21921e+11 accepted 0  lowest_f 2

(pid=77179) basinhopping step 9: f -6.47119e+11 trial_f -3.12629e+11 accepted 0  lowest_f -6.47119e+11
(pid=77429) basinhopping step 0: f -1.76802e+12
(pid=77480) basinhopping step 1: f 2.00581e+08 trial_f 2.70643e+08 accepted 0  lowest_f 2.00581e+08
(pid=77038) basinhopping step 4: f -2.84674e+11 trial_f -2.84674e+11 accepted 1  lowest_f -2.84674e+11
(pid=77038) found new global minimum on step 4 with function value -2.84674e+11
(pid=77428) basinhopping step 3: f -3.22007e+11 trial_f 1.41495e+08 accepted 0  lowest_f -3.22007e+11
(pid=77178) basinhopping step 2: f -2.89962e+13 trial_f -2.89962e+13 accepted 1  lowest_f -2.89962e+13
(pid=77178) found new global minimum on step 2 with function value -2.89962e+13
(pid=77122) basinhopping step 9: f -6.77871e+11 trial_f 7.27747e+08 accepted 0  lowest_f -6.77871e+11
(pid=77429) basinhopping step 1: f -1.76802e+12 trial_f 159860 accepted 0  lowest_f -1.76802e+12
(pid=77179) basinhopping step 10: f -6.47119e+11 trial_f 1.84585e+08 accepted 0  l

In [ ]:
for i in range(0,len(states)):    

    state=states[i]
    query = dfparam.query('state == "{}"'.format(state)).reset_index()
    parameters = np.array(query.iloc[:, 2:])[0]
    startdate,predict_range,s0,e0,a0,i0,r0,d0,startNCases,ratio,wcases,wrec = parameters
    Date = datetime.strptime(startdate, "%Y-%m-%d")
    end_date = Date + timedelta(days=+int(optimal[i][1]))
    dateStr=end_date.strftime("%Y-%m-%d")

    j = query['index'].values[0]
    dfparam.at[j, "s0"] = optimal[i][0]
    dfparam.at[j, "start-date"] = dateStr
    dfparam.at[j, "i0"] = optimal[i][2]
    dfparam.at[j, "WCASES"] = optimal[i][3]
    dfparam.at[j, "WREC"] = optimal[i][4]

    dfparam.to_csv("data/param_optimized_DE_Scipy.csv", sep=",", index=False)
    dfparam
    